# Session 5: Event-Driven Trading Bot

## Notebook 2: Order Management System (OMS)

**Learning Objectives:**
- Build a professional Order Management System
- Implement Market, Limit, and Stop order types
- Handle order lifecycle (pending → filled → complete)
- Integrate OMS with our event system
- Simulate exchange interactions

**Why This Matters:**
The OMS is the heart of any trading system. It's responsible for creating, tracking, and managing all orders. A robust OMS ensures your trades execute correctly and your bot stays in sync with the exchange.

---

## Quick Setup: Import Event System

Let's import the event system we built in Notebook 1:

In [1]:
# Import our event system from Notebook 1
from datetime import datetime
from typing import Dict, Any, List, Callable, Optional
from dataclasses import dataclass, field
from collections import deque
from threading import Lock
from enum import Enum
import json
import uuid
import time

# Re-create our basic Event system (copy from Notebook 1)
@dataclass
class Event:
    """Base class for all events in our trading system"""
    event_type: str
    data: Dict[str, Any]
    timestamp: datetime = None
    source: str = "unknown"
    
    def __post_init__(self):
        if self.timestamp is None:
            self.timestamp = datetime.now()

class EventQueue:
    """Central event queue from Notebook 1"""
    def __init__(self):
        self.events = deque()
        self.subscribers = {}
        self.lock = Lock()
        self.event_history = []
    
    def subscribe(self, event_type: str, callback: Callable[[Event], None]):
        with self.lock:
            if event_type not in self.subscribers:
                self.subscribers[event_type] = []
            self.subscribers[event_type].append(callback)
            print(f"✅ Subscribed to '{event_type}' events")
    
    def publish(self, event: Event):
        with self.lock:
            self.events.append(event)
            self.event_history.append(event)
            
            if event.event_type in self.subscribers:
                for callback in self.subscribers[event.event_type]:
                    try:
                        callback(event)
                    except Exception as e:
                        print(f"❌ Error in callback for {event.event_type}: {e}")
            
            print(f"📤 Published: {event.event_type} from {event.source}")

# Create our event queue
event_queue = EventQueue()
print("🏗️ Event system ready for OMS integration!")

🏗️ Event system ready for OMS integration!


## Part 1: Order States and Types

First, let's define the different order states and types our OMS will handle:

In [2]:
# Order States - lifecycle of an order
class OrderState(Enum):
    PENDING = "PENDING"           # Order created, waiting to be sent
    SUBMITTED = "SUBMITTED"       # Order sent to exchange
    OPEN = "OPEN"                 # Order active on exchange
    PARTIALLY_FILLED = "PARTIAL" # Order partially executed
    FILLED = "FILLED"             # Order completely executed
    CANCELLED = "CANCELLED"       # Order cancelled
    REJECTED = "REJECTED"         # Order rejected by exchange
    EXPIRED = "EXPIRED"           # Order expired (for time-limited orders)

# Order Types
class OrderType(Enum):
    MARKET = "MARKET"   # Execute immediately at current market price
    LIMIT = "LIMIT"     # Execute only at specified price or better
    STOP = "STOP"       # Convert to market order when stop price is hit
    STOP_LIMIT = "STOP_LIMIT"  # Convert to limit order when stop price is hit

# Order Side
class OrderSide(Enum):
    BUY = "BUY"
    SELL = "SELL"

print("📊 Order enums defined:")
print(f"States: {[state.value for state in OrderState]}")
print(f"Types: {[order_type.value for order_type in OrderType]}")
print(f"Sides: {[side.value for side in OrderSide]}")

📊 Order enums defined:
States: ['PENDING', 'SUBMITTED', 'OPEN', 'PARTIAL', 'FILLED', 'CANCELLED', 'REJECTED', 'EXPIRED']
Types: ['MARKET', 'LIMIT', 'STOP', 'STOP_LIMIT']
Sides: ['BUY', 'SELL']


## Part 2: Order Class

Now let's create a comprehensive Order class that tracks all order information:

In [3]:
@dataclass
class Order:
    """Comprehensive order class for our trading system"""
    
    # Core order information
    symbol: str
    side: OrderSide
    order_type: OrderType
    quantity: float
    
    # Optional price information
    price: Optional[float] = None          # For limit orders
    stop_price: Optional[float] = None     # For stop orders
    
    # Order tracking
    order_id: str = field(default_factory=lambda: str(uuid.uuid4()))
    client_order_id: str = field(default_factory=lambda: f"client_{int(time.time() * 1000)}")
    exchange_order_id: Optional[str] = None
    
    # Order state
    state: OrderState = OrderState.PENDING
    filled_quantity: float = 0.0
    remaining_quantity: Optional[float] = None
    average_fill_price: float = 0.0
    
    # Timestamps
    created_at: datetime = field(default_factory=datetime.now)
    submitted_at: Optional[datetime] = None
    filled_at: Optional[datetime] = None
    
    # Additional metadata
    fees_paid: float = 0.0
    notes: str = ""
    
    def __post_init__(self):
        """Initialize remaining quantity and validate order"""
        if self.remaining_quantity is None:
            self.remaining_quantity = self.quantity
        
        # Validate order
        self._validate()
    
    def _validate(self):
        """Validate order parameters"""
        if self.quantity <= 0:
            raise ValueError("Order quantity must be positive")
        
        if self.order_type in [OrderType.LIMIT, OrderType.STOP_LIMIT] and self.price is None:
            raise ValueError(f"{self.order_type.value} orders require a price")
        
        if self.order_type in [OrderType.STOP, OrderType.STOP_LIMIT] and self.stop_price is None:
            raise ValueError(f"{self.order_type.value} orders require a stop price")
    
    @property
    def is_buy(self) -> bool:
        return self.side == OrderSide.BUY
    
    @property
    def is_sell(self) -> bool:
        return self.side == OrderSide.SELL
    
    @property
    def is_filled(self) -> bool:
        return self.state == OrderState.FILLED
    
    @property
    def is_open(self) -> bool:
        return self.state in [OrderState.OPEN, OrderState.PARTIALLY_FILLED]
    
    @property
    def fill_percentage(self) -> float:
        """Percentage of order that has been filled"""
        return (self.filled_quantity / self.quantity) * 100 if self.quantity > 0 else 0
    
    def update_fill(self, fill_quantity: float, fill_price: float, fees: float = 0.0):
        """Update order with a partial or complete fill"""
        # Update quantities
        self.filled_quantity += fill_quantity
        self.remaining_quantity -= fill_quantity
        self.fees_paid += fees
        
        # Update average fill price (weighted average)
        if self.filled_quantity > 0:
            total_cost = (self.average_fill_price * (self.filled_quantity - fill_quantity)) + (fill_price * fill_quantity)
            self.average_fill_price = total_cost / self.filled_quantity
        
        # Update state
        if self.remaining_quantity <= 0:
            self.state = OrderState.FILLED
            self.filled_at = datetime.now()
        else:
            self.state = OrderState.PARTIALLY_FILLED
    
    def cancel(self):
        """Cancel the order"""
        if self.is_open:
            self.state = OrderState.CANCELLED
    
    def to_dict(self) -> Dict[str, Any]:
        """Convert order to dictionary for logging/API calls"""
        return {
            'order_id': self.order_id,
            'client_order_id': self.client_order_id,
            'symbol': self.symbol,
            'side': self.side.value,
            'type': self.order_type.value,
            'quantity': self.quantity,
            'price': self.price,
            'stop_price': self.stop_price,
            'state': self.state.value,
            'filled_quantity': self.filled_quantity,
            'remaining_quantity': self.remaining_quantity,
            'average_fill_price': self.average_fill_price,
            'fill_percentage': f"{self.fill_percentage:.1f}%",
            'created_at': self.created_at.isoformat(),
            'fees_paid': self.fees_paid
        }
    
    def __str__(self):
        price_str = f"@${self.price:.2f}" if self.price else "@MARKET"
        return f"{self.side.value} {self.quantity} {self.symbol} {price_str} ({self.state.value})"


# Test our Order class
print("🧪 Testing Order class:\n")

# Market order
market_order = Order("BTC/USDT", OrderSide.BUY, OrderType.MARKET, 0.1)
print(f"Market Order: {market_order}")

# Limit order
limit_order = Order("BTC/USDT", OrderSide.SELL, OrderType.LIMIT, 0.05, price=45000)
print(f"Limit Order: {limit_order}")

# Stop order
stop_order = Order("BTC/USDT", OrderSide.SELL, OrderType.STOP, 0.08, stop_price=42000)
print(f"Stop Order: {stop_order}")

print(f"\n📊 Market order details:")
print(json.dumps(market_order.to_dict(), indent=2, default=str))

🧪 Testing Order class:

Market Order: BUY 0.1 BTC/USDT @MARKET (PENDING)
Limit Order: SELL 0.05 BTC/USDT @$45000.00 (PENDING)
Stop Order: SELL 0.08 BTC/USDT @MARKET (PENDING)

📊 Market order details:
{
  "order_id": "aab41f17-faa2-4d5e-ad50-2689e3c8b689",
  "client_order_id": "client_1750871237729",
  "symbol": "BTC/USDT",
  "side": "BUY",
  "type": "MARKET",
  "quantity": 0.1,
  "price": null,
  "stop_price": null,
  "state": "PENDING",
  "filled_quantity": 0.0,
  "remaining_quantity": 0.1,
  "average_fill_price": 0.0,
  "fill_percentage": "0.0%",
  "created_at": "2025-06-25T19:07:17.729210",
  "fees_paid": 0.0
}


## Part 3: Order Events

Let's create specific events for order management that integrate with our event system:

In [4]:
class OrderRequestEvent(Event):
    """Event to request creation of a new order"""
    def __init__(self, order: Order, source: str = "strategy"):
        super().__init__(
            event_type="order_request",
            data={
                "order": order,
                "order_dict": order.to_dict()
            },
            source=source
        )

class OrderStatusEvent(Event):
    """Event for order status updates"""
    def __init__(self, order: Order, status_type: str, message: str = "", source: str = "oms"):
        super().__init__(
            event_type="order_status",
            data={
                "order_id": order.order_id,
                "status_type": status_type,  # 'submitted', 'filled', 'cancelled', etc.
                "message": message,
                "order_state": order.state.value,
                "order": order
            },
            source=source
        )

class OrderFillEvent(Event):
    """Event for order fills (partial or complete)"""
    def __init__(self, order: Order, fill_quantity: float, fill_price: float, fees: float = 0.0, source: str = "exchange"):
        super().__init__(
            event_type="order_fill",
            data={
                "order_id": order.order_id,
                "symbol": order.symbol,
                "side": order.side.value,
                "fill_quantity": fill_quantity,
                "fill_price": fill_price,
                "fees": fees,
                "order": order,
                "is_complete_fill": (order.remaining_quantity - fill_quantity) <= 0
            },
            source=source
        )

class OrderErrorEvent(Event):
    """Event for order errors and rejections"""
    def __init__(self, order: Order, error_type: str, error_message: str, source: str = "oms"):
        super().__init__(
            event_type="order_error",
            data={
                "order_id": order.order_id,
                "error_type": error_type,
                "error_message": error_message,
                "order": order
            },
            source=source
        )

# Test order events
print("📧 Testing Order Events:\n")

test_order = Order("BTC/USDT", OrderSide.BUY, OrderType.LIMIT, 0.1, price=43000)

# Order request event
request_event = OrderRequestEvent(test_order, "algorithm")
print(f"Request Event: {request_event.event_type} from {request_event.source}")

# Order status event
status_event = OrderStatusEvent(test_order, "submitted", "Order sent to exchange")
print(f"Status Event: {status_event.event_type} - {status_event.data['status_type']}")

# Order fill event
fill_event = OrderFillEvent(test_order, 0.05, 42950, 2.50)
print(f"Fill Event: {fill_event.event_type} - {fill_event.data['fill_quantity']} @ ${fill_event.data['fill_price']}")

📧 Testing Order Events:

Request Event: order_request from algorithm
Status Event: order_status - submitted
Fill Event: order_fill - 0.05 @ $42950


## Part 4: Order Management System

Now let's build the core OMS that manages all orders and integrates with our event system:

In [5]:
class OrderManager:
    """Professional Order Management System"""
    
    def __init__(self, event_queue: EventQueue):
        self.event_queue = event_queue
        self.name = "order_manager"
        
        # Order storage
        self.orders: Dict[str, Order] = {}  # order_id -> Order
        self.orders_by_symbol: Dict[str, List[str]] = {}  # symbol -> [order_ids]
        self.open_orders: List[str] = []  # Active order IDs
        
        # Statistics
        self.total_orders_created = 0
        self.total_orders_filled = 0
        self.total_orders_cancelled = 0
        
        # Subscribe to order-related events
        self.event_queue.subscribe("order_request", self.on_order_request)
        self.event_queue.subscribe("order_fill", self.on_order_fill)
        
        print(f"🏢 {self.name}: Order Management System initialized")
    
    def create_order(self, symbol: str, side: OrderSide, order_type: OrderType, 
                    quantity: float, price: float = None, stop_price: float = None) -> Order:
        """Create a new order"""
        try:
            order = Order(
                symbol=symbol,
                side=side,
                order_type=order_type,
                quantity=quantity,
                price=price,
                stop_price=stop_price
            )
            
            # Store order
            self.orders[order.order_id] = order
            
            # Track by symbol
            if symbol not in self.orders_by_symbol:
                self.orders_by_symbol[symbol] = []
            self.orders_by_symbol[symbol].append(order.order_id)
            
            # Add to open orders
            self.open_orders.append(order.order_id)
            
            # Update stats
            self.total_orders_created += 1
            
            print(f"📝 {self.name}: Created order {order.order_id[:8]}... - {order}")
            
            # Publish order status event
            status_event = OrderStatusEvent(order, "created", "Order created successfully", self.name)
            self.event_queue.publish(status_event)
            
            return order
            
        except Exception as e:
            print(f"❌ {self.name}: Failed to create order - {e}")
            return None
    
    def on_order_request(self, event: Event):
        """Handle order request events"""
        order_data = event.data["order"]
        print(f"📥 {self.name}: Received order request from {event.source}")
        
        # For this demo, we'll directly process the order
        # In real system, this would validate and send to exchange
        order = order_data
        
        # Store the order
        self.orders[order.order_id] = order
        if order.symbol not in self.orders_by_symbol:
            self.orders_by_symbol[order.symbol] = []
        self.orders_by_symbol[order.symbol].append(order.order_id)
        self.open_orders.append(order.order_id)
        self.total_orders_created += 1
        
        # Update order state
        order.state = OrderState.SUBMITTED
        order.submitted_at = datetime.now()
        
        # Publish status update
        status_event = OrderStatusEvent(order, "submitted", "Order submitted to exchange", self.name)
        self.event_queue.publish(status_event)
    
    def on_order_fill(self, event: Event):
        """Handle order fill events from exchange"""
        order_id = event.data["order_id"]
        fill_quantity = event.data["fill_quantity"]
        fill_price = event.data["fill_price"]
        fees = event.data.get("fees", 0.0)
        
        if order_id not in self.orders:
            print(f"⚠️ {self.name}: Received fill for unknown order {order_id}")
            return
        
        order = self.orders[order_id]
        print(f"💰 {self.name}: Processing fill for {order_id[:8]}... - {fill_quantity} @ ${fill_price}")
        
        # Update order with fill
        order.update_fill(fill_quantity, fill_price, fees)
        
        # If order is completely filled, remove from open orders
        if order.is_filled and order_id in self.open_orders:
            self.open_orders.remove(order_id)
            self.total_orders_filled += 1
            print(f"✅ {self.name}: Order {order_id[:8]}... completely filled!")
        
        # Publish status update
        status_type = "filled" if order.is_filled else "partially_filled"
        message = f"Fill: {fill_quantity} @ ${fill_price} (Total: {order.filled_quantity}/{order.quantity})"
        status_event = OrderStatusEvent(order, status_type, message, self.name)
        self.event_queue.publish(status_event)
    
    def cancel_order(self, order_id: str) -> bool:
        """Cancel an order"""
        if order_id not in self.orders:
            print(f"⚠️ {self.name}: Cannot cancel unknown order {order_id}")
            return False
        
        order = self.orders[order_id]
        if not order.is_open:
            print(f"⚠️ {self.name}: Cannot cancel order {order_id[:8]}... - not open ({order.state.value})")
            return False
        
        order.cancel()
        if order_id in self.open_orders:
            self.open_orders.remove(order_id)
        
        self.total_orders_cancelled += 1
        print(f"🚫 {self.name}: Cancelled order {order_id[:8]}...")
        
        # Publish status update
        status_event = OrderStatusEvent(order, "cancelled", "Order cancelled by user", self.name)
        self.event_queue.publish(status_event)
        
        return True
    
    def get_orders(self, symbol: str = None, state: OrderState = None) -> List[Order]:
        """Get orders with optional filtering"""
        orders = list(self.orders.values())
        
        if symbol:
            orders = [o for o in orders if o.symbol == symbol]
        
        if state:
            orders = [o for o in orders if o.state == state]
        
        return orders
    
    def get_stats(self) -> Dict[str, Any]:
        """Get OMS statistics"""
        return {
            "total_orders_created": self.total_orders_created,
            "total_orders_filled": self.total_orders_filled,
            "total_orders_cancelled": self.total_orders_cancelled,
            "open_orders_count": len(self.open_orders),
            "symbols_traded": list(self.orders_by_symbol.keys()),
            "orders_by_state": {
                state.value: len([o for o in self.orders.values() if o.state == state])
                for state in OrderState
            }
        }

# Create our Order Management System
oms = OrderManager(event_queue)
print(f"\n📊 OMS Stats: {json.dumps(oms.get_stats(), indent=2)}")

✅ Subscribed to 'order_request' events
✅ Subscribed to 'order_fill' events
🏢 order_manager: Order Management System initialized

📊 OMS Stats: {
  "total_orders_created": 0,
  "total_orders_filled": 0,
  "total_orders_cancelled": 0,
  "open_orders_count": 0,
  "symbols_traded": [],
  "orders_by_state": {
    "PENDING": 0,
    "SUBMITTED": 0,
    "OPEN": 0,
    "PARTIAL": 0,
    "FILLED": 0,
    "CANCELLED": 0,
    "REJECTED": 0,
    "EXPIRED": 0
  }
}


## Part 5: Mock Exchange Simulator

Let's create a simple exchange simulator to test our OMS:

In [6]:
import random

class MockExchange:
    """Simple exchange simulator for testing our OMS"""
    
    def __init__(self, event_queue: EventQueue):
        self.event_queue = event_queue
        self.name = "mock_exchange"
        
        # Mock market prices
        self.market_prices = {
            "BTC/USDT": 43250.00,
            "ETH/USDT": 2650.00,
            "BNB/USDT": 310.00
        }
        
        # Exchange settings
        self.trading_fee = 0.001  # 0.1% trading fee
        self.fill_probability = 0.8  # 80% chance orders get filled
        
        # Subscribe to order status events to simulate fills
        self.event_queue.subscribe("order_status", self.on_order_status)
        
        print(f"🏪 {self.name}: Mock Exchange initialized")
        print(f"   Current prices: {self.market_prices}")
    
    def update_price(self, symbol: str, new_price: float):
        """Update market price for a symbol"""
        old_price = self.market_prices.get(symbol, 0)
        self.market_prices[symbol] = new_price
        change = ((new_price - old_price) / old_price * 100) if old_price > 0 else 0
        print(f"📈 {self.name}: {symbol} price updated: ${old_price:,.2f} → ${new_price:,.2f} ({change:+.2f}%)")
    
    def on_order_status(self, event: Event):
        """React to order status events and simulate fills"""
        if event.data["status_type"] != "submitted":
            return  # Only process newly submitted orders
        
        order = event.data["order"]
        
        # Simulate some processing delay
        time.sleep(0.1)
        
        print(f"🏪 {self.name}: Processing order {order.order_id[:8]}... - {order}")
        
        # Simulate order execution based on type
        if order.order_type == OrderType.MARKET:
            self._fill_market_order(order)
        elif order.order_type == OrderType.LIMIT:
            self._process_limit_order(order)
        elif order.order_type == OrderType.STOP:
            self._process_stop_order(order)
    
    def _fill_market_order(self, order: Order):
        """Fill market order immediately at current price"""
        if order.symbol not in self.market_prices:
            error_event = OrderErrorEvent(order, "invalid_symbol", f"Unknown symbol: {order.symbol}", self.name)
            self.event_queue.publish(error_event)
            return
        
        # Market orders fill immediately at current market price with some slippage
        market_price = self.market_prices[order.symbol]
        slippage = random.uniform(-0.005, 0.005)  # ±0.5% slippage
        fill_price = market_price * (1 + slippage)
        
        # Calculate fees
        fees = order.quantity * fill_price * self.trading_fee
        
        # Create fill event
        fill_event = OrderFillEvent(order, order.quantity, fill_price, fees, self.name)
        self.event_queue.publish(fill_event)
        
        print(f"   ✅ Market order filled: {order.quantity} @ ${fill_price:.2f} (fees: ${fees:.2f})")
    
    def _process_limit_order(self, order: Order):
        """Process limit order - fill if price is favorable"""
        if order.symbol not in self.market_prices:
            error_event = OrderErrorEvent(order, "invalid_symbol", f"Unknown symbol: {order.symbol}", self.name)
            self.event_queue.publish(error_event)
            return
        
        market_price = self.market_prices[order.symbol]
        
        # Check if limit order can be filled immediately
        can_fill = False
        if order.is_buy and market_price <= order.price:  # Buy limit can fill if market price is at or below limit
            can_fill = True
        elif order.is_sell and market_price >= order.price:  # Sell limit can fill if market price is at or above limit
            can_fill = True
        
        if can_fill and random.random() < self.fill_probability:
            # Fill at the limit price (or better)
            fill_price = min(order.price, market_price) if order.is_buy else max(order.price, market_price)
            fees = order.quantity * fill_price * self.trading_fee
            
            fill_event = OrderFillEvent(order, order.quantity, fill_price, fees, self.name)
            self.event_queue.publish(fill_event)
            
            print(f"   ✅ Limit order filled: {order.quantity} @ ${fill_price:.2f} (limit: ${order.price:.2f})")
        else:
            # Order remains open on the book
            order.state = OrderState.OPEN
            print(f"   📋 Limit order placed on book: {order.quantity} @ ${order.price:.2f} (market: ${market_price:.2f})")
    
    def _process_stop_order(self, order: Order):
        """Process stop order - becomes market order when triggered"""
        if order.symbol not in self.market_prices:
            error_event = OrderErrorEvent(order, "invalid_symbol", f"Unknown symbol: {order.symbol}", self.name)
            self.event_queue.publish(error_event)
            return
        
        market_price = self.market_prices[order.symbol]
        
        # Check if stop is triggered
        triggered = False
        if order.is_buy and market_price >= order.stop_price:  # Buy stop triggered when price goes up
            triggered = True
        elif order.is_sell and market_price <= order.stop_price:  # Sell stop triggered when price goes down
            triggered = True
        
        if triggered:
            print(f"   🚨 Stop order triggered at ${market_price:.2f} (stop: ${order.stop_price:.2f})")
            # Convert to market order and fill
            slippage = random.uniform(-0.005, 0.005)
            fill_price = market_price * (1 + slippage)
            fees = order.quantity * fill_price * self.trading_fee
            
            fill_event = OrderFillEvent(order, order.quantity, fill_price, fees, self.name)
            self.event_queue.publish(fill_event)
            
            print(f"   ✅ Stop order filled as market: {order.quantity} @ ${fill_price:.2f}")
        else:
            order.state = OrderState.OPEN
            print(f"   📋 Stop order waiting: trigger @ ${order.stop_price:.2f} (market: ${market_price:.2f})")

# Create mock exchange
exchange = MockExchange(event_queue)
print("\n🏪 Mock Exchange ready for testing!")

✅ Subscribed to 'order_status' events
🏪 mock_exchange: Mock Exchange initialized
   Current prices: {'BTC/USDT': 43250.0, 'ETH/USDT': 2650.0, 'BNB/USDT': 310.0}

🏪 Mock Exchange ready for testing!


## Part 6: Complete OMS Demo

Let's test our complete Order Management System with different order types!

In [7]:
print("🎬 DEMO: Complete Order Management System\n")
print("=" * 70)

# Test 1: Market Order
print("\n📊 Test 1: Market Order")
print("-" * 30)
market_order = oms.create_order("BTC/USDT", OrderSide.BUY, OrderType.MARKET, 0.1)
if market_order:
    # Publish order request to trigger exchange processing
    request_event = OrderRequestEvent(market_order, "demo")
    event_queue.publish(request_event)

time.sleep(1)  # Allow processing

# Test 2: Limit Order (should fill immediately)
print("\n📊 Test 2: Limit Order (Favorable Price)")
print("-" * 40)
current_btc_price = exchange.market_prices["BTC/USDT"]
limit_order = oms.create_order("BTC/USDT", OrderSide.BUY, OrderType.LIMIT, 0.05, price=current_btc_price + 100)  # Above market
if limit_order:
    request_event = OrderRequestEvent(limit_order, "demo")
    event_queue.publish(request_event)

time.sleep(1)

# Test 3: Limit Order (won't fill)
print("\n📊 Test 3: Limit Order (Too Low)")
print("-" * 30)
low_limit_order = oms.create_order("BTC/USDT", OrderSide.BUY, OrderType.LIMIT, 0.08, price=current_btc_price - 1000)  # Well below market
if low_limit_order:
    request_event = OrderRequestEvent(low_limit_order, "demo")
    event_queue.publish(request_event)

time.sleep(1)

# Test 4: Stop Order
print("\n📊 Test 4: Stop Order")
print("-" * 20)
stop_order = oms.create_order("BTC/USDT", OrderSide.SELL, OrderType.STOP, 0.03, stop_price=current_btc_price - 500)
if stop_order:
    request_event = OrderRequestEvent(stop_order, "demo")
    event_queue.publish(request_event)

time.sleep(1)

# Test 5: Price Movement to Trigger Stop
print("\n📊 Test 5: Price Movement (Trigger Stop)")
print("-" * 35)
new_price = current_btc_price - 600  # Drop price to trigger stop
exchange.update_price("BTC/USDT", new_price)

# Re-process stop order with new price
if stop_order and stop_order.state == OrderState.OPEN:
    print(f"🔄 Re-checking stop order against new price...")
    exchange._process_stop_order(stop_order)

time.sleep(1)

# Test 6: Cancel an order
print("\n📊 Test 6: Cancel Order")
print("-" * 20)
if low_limit_order and low_limit_order.is_open:
    oms.cancel_order(low_limit_order.order_id)

print("\n" + "=" * 70)
print("📈 Final OMS Statistics:")
print(json.dumps(oms.get_stats(), indent=2))

print("\n📋 All Orders Summary:")
for order in oms.orders.values():
    print(f"  • {order.order_id[:8]}... - {order} - {order.fill_percentage:.1f}% filled")

print(f"\n📊 Total Events Processed: {len(event_queue.event_history)}")

🎬 DEMO: Complete Order Management System


📊 Test 1: Market Order
------------------------------
📝 order_manager: Created order 5c53cc3e... - BUY 0.1 BTC/USDT @MARKET (PENDING)
📤 Published: order_status from order_manager
📥 order_manager: Received order request from demo


KeyboardInterrupt: 

## Part 7: Your Turn - Advanced Exercise

**Challenge:** Extend the OMS with advanced features!

Choose one or more of these challenges:

1. **Order Modification**: Add ability to modify price/quantity of open orders
2. **Order Expiration**: Add time-based order expiration
3. **Bracket Orders**: Create orders with both profit target and stop loss
4. **Order Validation**: Add more sophisticated validation (min/max quantities, price bands)
5. **Partial Fill Handling**: Better handling of multiple partial fills

In [ ]:
# Challenge 1: Order Modification
def modify_order_price(oms: OrderManager, order_id: str, new_price: float):
    """Modify the price of an open order"""
    # YOUR CODE HERE
    pass

# Challenge 2: Order Expiration
from datetime import timedelta

def add_expiration_to_order(order: Order, minutes: int):
    """Add expiration time to an order"""
    # YOUR CODE HERE
    pass

def check_expired_orders(oms: OrderManager):
    """Check for and cancel expired orders"""
    # YOUR CODE HERE
    pass

# Challenge 3: Bracket Order
def create_bracket_order(oms: OrderManager, symbol: str, side: OrderSide, quantity: float, 
                        entry_price: float, profit_target: float, stop_loss: float):
    """Create a bracket order (entry + profit target + stop loss)"""
    # YOUR CODE HERE
    pass

# Test your implementations here
print("🧪 Test your advanced features here!")

## Congratulations!

You've built a professional-grade Order Management System! Here's what you accomplished:

✅ **Complete Order Types**: Market, Limit, and Stop orders with full lifecycle management  
✅ **Event Integration**: OMS communicates through events for loose coupling  
✅ **Order Tracking**: Complete state management from creation to completion  
✅ **Exchange Simulation**: Realistic order processing and fills  
✅ **Error Handling**: Proper validation and error events  
✅ **Statistics & Monitoring**: Complete order tracking and reporting  

## Key Professional Features:

1. **Order States**: Proper lifecycle management (PENDING → SUBMITTED → FILLED)
2. **Event-Driven**: Loose coupling through event system
3. **Fill Handling**: Partial and complete fills with average price calculation
4. **Order Validation**: Input validation and error handling
5. **Statistics**: Comprehensive tracking and reporting

## Next Steps:

In the next notebook, we'll build the **Portfolio Manager** and **Risk Controller** that work with this OMS to create a complete trading system!

---
*"Professional trading systems are built on robust order management."* 📋💰